# jovian-ml-project

Use the "Run" button to execute the code.

In [1]:
!pip install jovian --upgrade --quiet

You should consider upgrading via the 'c:\users\anubr\anaconda3\envs\datascience\python.exe -m pip install --upgrade pip' command.


In [2]:
import jovian

In [3]:
# Execute this to save new versions of the notebook
jovian.commit(project="jovian-ml-project",filename="jovian-ml-project")

<IPython.core.display.Javascript object>

[jovian] Attempting to save notebook..
[jovian] Please enter your API key ( from https://jovian.ai/ ):
API KEY: ········
[jovian] Updating notebook "anubratadas/jovian-ml-project" on https://jovian.ai/
[jovian] Uploading notebook..
[jovian] Capturing environment..


[jovian] Error: Failed to read Anaconda environment using command: "conda env export -n base --no-builds"


[jovian] Committed successfully! https://jovian.ai/anubratadas/jovian-ml-project


'https://jovian.ai/anubratadas/jovian-ml-project'

In [35]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import requests
import xml.etree.ElementTree as ET
import time
import re
from nltk.corpus import stopwords
from nltk.corpus import words
%matplotlib inline
from tqdm import tqdm

In [2]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import warnings
warnings.simplefilter(action='ignore')

In [36]:
train_text_df = pd.read_csv('training_text.zip', sep="\|\|", encoding="utf-8",engine="python", skiprows=1, names=["ID", "Text"],compression='zip')

In [4]:
test_text_df = pd.read_csv('test_text.zip', sep="\|\|", encoding="utf-8",engine="python", skiprows=1, names=["ID", "Text"],compression='zip')

In [5]:
train_vari_df = pd.read_csv('training_variants.zip',compression='zip')
test_vari_df  = pd.read_csv('test_variants.zip',compression='zip')

In [6]:
import string
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [7]:
revised_punctuation='!"#$%&\'()*+,./:;<=>?@[\\]^_`{|}~'

In [14]:
import nltk
nltk.download('words')

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\anubr\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


True

In [9]:
nltk_words=set(words.words())

In [22]:
len(nltk_words)

235892

In [15]:
nltk.download('brown')

[nltk_data] Downloading package brown to
[nltk_data]     C:\Users\anubr\AppData\Roaming\nltk_data...
[nltk_data]   Package brown is already up-to-date!


True

In [20]:
from nltk.corpus import brown
brown_words = brown.words()

In [21]:
len(brown_words)

1161192

In [37]:
train_text_df['cleaned_text'] = 'NA'

In [38]:
# train_text_df['text_count'] = 'NA'
# train_text_df.rename(columns={"text_count":"cleaned_text"},inplace=True)
train_text_df.head()

ID                                               Text cleaned_text
0   0  Cyclin-dependent kinases (CDKs) regulate a var...           NA
1   1   Abstract Background  Non-small cell lung canc...           NA
2   2   Abstract Background  Non-small cell lung canc...           NA
3   3  Recent evidence has demonstrated that acquired...           NA
4   4  Oncogenic mutations in the monomeric Casitas B...           NA

In [34]:
# removal of non scientific words. i have realized we need to remove all nonscientific words
# nltk word corpus
def cleanse_data_nltk(text):        
    if isinstance(text,str):
        #no_punctuation = [char for char in text.replace('\n',' ') if char not in revised_punctuation]
        #no_punctuation_txt = ''.join(no_punctuation)
        #text_words=[word for word in no_punctuation_txt.split()]
        text_words=[word for word in text.split()]
        text_words=[word for word in text_words if word not in nltk_words]
        text=" ".join(text_words)
        yield text
    else:
        yield 'NA'

In [33]:
# removal of non scientific words. i have realized we need to remove all nonscientific words
# brown word corpus
def cleanse_data_brown(text):        
    if isinstance(text,str):
        #no_punctuation = [char for char in text.replace('\n',' ') if char not in revised_punctuation]
        #no_punctuation_txt = ''.join(no_punctuation)
        #text_words=[word for word in no_punctuation_txt.split()]
        text_words=[word for word in text.split()]
        text_words=[word for word in text_words if word not in brown_words]
        text=" ".join(text_words)
        yield text
    else:
        yield 'NA'

In [39]:
# use of a generator 
for index,row in tqdm(train_text_df.iterrows()):
    text=row[1]
    result=cleanse_data_nltk(text)
    train_text_df['cleaned_text'][index] = next(result)

3321it [00:19, 174.24it/s]


In [28]:
'kinase' in brown_words

False

In [40]:
train_text_df.head()

ID                                               Text  \
0   0  Cyclin-dependent kinases (CDKs) regulate a var...   
1   1   Abstract Background  Non-small cell lung canc...   
2   2   Abstract Background  Non-small cell lung canc...   
3   3  Recent evidence has demonstrated that acquired...   
4   4  Oncogenic mutations in the monomeric Casitas B...   

                                        cleaned_text  
0  Cyclin-dependent kinases (CDKs) processes. CDK...  
1  Abstract Background Non-small (NSCLC) disorder...  
2  Abstract Background Non-small (NSCLC) disorder...  
3  Recent has demonstrated disomy (aUPD) mutation...  
4  Oncogenic mutations Casitas B-lineage (Cbl) tu...

In [59]:
list(map(lambda x:len(x),['roger']))

[5]

In [64]:
train_text_df['text_len']=train_text_df['Text'].map(lambda x:len(x),na_action='ignore')
train_text_df['clean_text_len']=train_text_df['cleaned_text'].map(lambda x:len(x),na_action='ignore')

In [65]:
train_text_df.head()

ID                                               Text  \
0   0  Cyclin-dependent kinases (CDKs) regulate a var...   
1   1   Abstract Background  Non-small cell lung canc...   
2   2   Abstract Background  Non-small cell lung canc...   
3   3  Recent evidence has demonstrated that acquired...   
4   4  Oncogenic mutations in the monomeric Casitas B...   

                                        cleaned_text  text_len  clean_text_len  
0  Cyclin-dependent kinases (CDKs) processes. CDK...   39672.0           20462  
1  Abstract Background Non-small (NSCLC) disorder...   36691.0           18897  
2  Abstract Background Non-small (NSCLC) disorder...   36691.0           18897  
3  Recent has demonstrated disomy (aUPD) mutation...   36238.0           17618  
4  Oncogenic mutations Casitas B-lineage (Cbl) tu...   41308.0           19425

In [16]:
from nltk.corpus import stopwords
stopwords=stopwords.words('english')

In [34]:
# set did not help as it reduces the number to 
def reduce_words(row,index): 
    text=row[1]
    if isinstance(text,str):
        new_text_words = set(text.split())
        
        important_words = new_text_words.difference(words)
        edited_words = " ".join(important_words)
        train_text_df['new_text'][index] = edited_words        

In [27]:
train_text_df['text_count']='NA'

In [14]:
from collections import Counter

In [31]:
def word_count(text):
    if isinstance(text,str):
        words=text.split()
        word_count=Counter(words)
        yield word_count
    else:
        yield "NA"

In [32]:
# use of a generator 
for index,row in train_text_df.iterrows():
    text=row[1]
    result=word_count(text)
    train_text_df['text_count'][index] = next(result)

In [66]:
'finally' in nltk_words

True

In [54]:
from nltk.probability import FreqDist

In [67]:
for text in train_text_df['Text']:
    text=text.split()    
    freq_text=FreqDist(text)
    for key in freq_text:
        if key not in nltk_words:
            print(freq_text.items())
    break

dict_items([('Cyclin-dependent', 1), ('kinases', 2), ('(CDKs)', 2), ('regulate', 2), ('a', 128), ('variety', 3), ('of', 209), ('fundamental', 2), ('cellular', 3), ('processes.', 1), ('CDK10', 64), ('stands', 1), ('out', 6), ('as', 33), ('one', 5), ('the', 224), ('last', 2), ('orphan', 3), ('CDKs', 4), ('for', 19), ('which', 23), ('no', 8), ('activating', 2), ('cyclin', 82), ('has', 9), ('been', 10), ('identified', 8), ('and', 208), ('kinase', 16), ('activity', 7), ('revealed.', 1), ('Previous', 2), ('work', 1), ('shown', 13), ('that', 52), ('silencing', 16), ('increases', 2), ('ETS2', 44), ('(v-ets', 2), ('erythroblastosis', 2), ('virus', 2), ('E26', 2), ('oncogene', 2), ('homolog', 2), ('2)-driven', 1), ('activation', 1), ('MAPK', 3), ('pathway,', 2), ('confers', 1), ('tamoxifen', 6), ('resistance', 6), ('to', 79), ('breast', 6), ('cancer', 8), ('cells.', 8), ('The', 29), ('precise', 1), ('mechanisms', 4), ('by', 43), ('modulates', 1), ('activity,', 3), ('more', 1), ('generally', 1), 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




dict_items([('Cyclin-dependent', 1), ('kinases', 2), ('(CDKs)', 2), ('regulate', 2), ('a', 128), ('variety', 3), ('of', 209), ('fundamental', 2), ('cellular', 3), ('processes.', 1), ('CDK10', 64), ('stands', 1), ('out', 6), ('as', 33), ('one', 5), ('the', 224), ('last', 2), ('orphan', 3), ('CDKs', 4), ('for', 19), ('which', 23), ('no', 8), ('activating', 2), ('cyclin', 82), ('has', 9), ('been', 10), ('identified', 8), ('and', 208), ('kinase', 16), ('activity', 7), ('revealed.', 1), ('Previous', 2), ('work', 1), ('shown', 13), ('that', 52), ('silencing', 16), ('increases', 2), ('ETS2', 44), ('(v-ets', 2), ('erythroblastosis', 2), ('virus', 2), ('E26', 2), ('oncogene', 2), ('homolog', 2), ('2)-driven', 1), ('activation', 1), ('MAPK', 3), ('pathway,', 2), ('confers', 1), ('tamoxifen', 6), ('resistance', 6), ('to', 79), ('breast', 6), ('cancer', 8), ('cells.', 8), ('The', 29), ('precise', 1), ('mechanisms', 4), ('by', 43), ('modulates', 1), ('activity,', 3), ('more', 1), ('generally', 1),

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [33]:
train_text_df.head()

ID                                               Text  \
0   0  Cyclin-dependent kinases (CDKs) regulate a var...   
1   1   Abstract Background  Non-small cell lung canc...   
2   2   Abstract Background  Non-small cell lung canc...   
3   3  Recent evidence has demonstrated that acquired...   
4   4  Oncogenic mutations in the monomeric Casitas B...   

                                          text_count  
0  {'Cyclin-dependent': 1, 'kinases': 2, '(CDKs)'...  
1  {'Abstract': 1, 'Background': 1, 'Non-small': ...  
2  {'Abstract': 1, 'Background': 1, 'Non-small': ...  
3  {'Recent': 1, 'evidence': 4, 'has': 7, 'demons...  
4  {'Oncogenic': 2, 'mutations': 126, 'in': 145, ...

In [13]:
# removal of stopwords. i have realized we need to remove all nonscientific words
def cleanse_data(data):        
    if isinstance(data,str):
        no_punctuation = [char for char in data.replace('\n',' ') if char not in revised_punctuation]
        no_punctuation_txt = ''.join(no_punctuation)
        text_words=[word for word in no_punctuation_txt.split()]
        text_words=[word for word in text_words if word not in stopwords]
        text=" ".join(text_words)
        return text

In [17]:
train_text_df['new_text']=train_text_df['Text'].map(cleanse_data)

In [18]:
train_text_df.head()

ID                                               Text  \
0   0  Cyclin-dependent kinases (CDKs) regulate a var...   
1   1   Abstract Background  Non-small cell lung canc...   
2   2   Abstract Background  Non-small cell lung canc...   
3   3  Recent evidence has demonstrated that acquired...   
4   4  Oncogenic mutations in the monomeric Casitas B...   

                                            new_text  
0  Cyclin-dependent,kinases,CDKs,regulate,variety...  
1  Abstract,Background,Non-small,cell,lung,cancer...  
2  Abstract,Background,Non-small,cell,lung,cancer...  
3  Recent,evidence,demonstrated,acquired,uniparen...  
4  Oncogenic,mutations,monomeric,Casitas,B-lineag...

In [22]:
from nltk.probability import FreqDist

we have obtained the frequency distribution of words using freqdist

In [37]:
def freq_dist(data):
    data=data.split(",")
    freq=FreqDist(data)
    # sorting dictionary based on values
    freq=sorted(freq.items(),key=lambda x:x[1], reverse=True)
    return freq

In [27]:
FreqDist(train_text_df.loc[1,'new_text'].split(","))

FreqDist({'c-CBL': 152, 'mutations': 63, 'lung': 53, 'EGFR': 43, 'cell': 41, 'mutation': 40, 'The': 37, 'MET': 33, 'cells': 32, 'cancer': 31, ...})

In [29]:
test_var=train_text_df.loc[0:5]

In [38]:
train_text_df['new_text'].map(freq_dist)

0    [(M, 92), (cyclin, 84), (CDK10, 76), (Fig, 63)...
1    [(c-CBL, 152), (mutations, 63), (lung, 53), (E...
2    [(c-CBL, 152), (mutations, 63), (lung, 53), (E...
3    [(CBL, 99), (mutations, 67), (cases, 48), (aUP...
4    [(mutations, 149), (CBL, 119), (cancer, 60), (...
5    [(mutations, 149), (CBL, 119), (cancer, 60), (...
Name: new_text, dtype: object

we have sorted the frequency dictionary based on values using the key parameter of sorted and higher values first using reverse

In [ ]:
sorted(test_dic.items(),key=lambda x:x[1], reverse=True)

In [ ]:
#cleanse_data(data)

In [ ]:
#len(data.split('\n'))

In [ ]:
#scan_data1=[i[:200] for i in data]

In [ ]:
len(scan_data1)

In [ ]:
for i in range(10):
    print(scan_data1[i])

In [ ]:
cd /content

In [ ]:
pa_tree=ET.parse('pa2021.xml')

In [ ]:
root=pa_tree.getroot()

In [ ]:
# for child in root:
#   print(child.tag)

In [ ]:
for element_1 in root:
  #print("---------level_1-----------")
  #print(element_1.tag)
  
  for element_2 in element_1:
    #print("---------level_2-----------")
    #print("    "+element_2.tag," ",element_2.text)
    
    for element_3 in element_2:
      #print("---------level_3-----------")
      #print("        "+element_3.tag," ",element_3.text)
      
      for element_4 in element_3:
        #print("---------level_4-----------")
        if element_4.tag=="String":
          print("                   "+element_4.tag," ",element_4.text)
          
  #break
    

In [ ]:
len(root)

In [ ]:
desc_tree=ET.parse('desc2021.xml')

In [ ]:
desc_root=desc_tree.getroot()

In [ ]:
len(desc_root)

In [ ]:
term_description=[]
for element_1 in desc_root:
  #print("-------level_1----------")
  #print(element_1.tag," ",element_1.text)
  for element_2 in element_1:
    #print("    ----------level_2----------")
    #print("    "+element_2.tag," ",element_2.text)
    for element_3 in element_2:
      if element_3.tag=='String':
        #print("        ---------level_3--------")
        #print("        "+element_3.tag," ",element_3.text)
        term_description.append(element_3.text)

  #break

In [ ]:
len(term_description)

In [ ]:
term_description[:10]

In [ ]:
import csv 
with open('term_description.csv', 'w') as f: 
    write = csv.writer(f) 
    write.writerow(term_description) 
    

There are 2 ways to remove punctuation. one is to use the string library punctuation module on the text before tokenization, the other is to use the nltk.punct library

In [ ]:
len(scan_data1[1])

In [ ]:
#nltk.word_tokenize(scan_data1[1])

In [ ]:
# import string punctuation
import string
string.punctuation

In [ ]:
len(cleanup_text(scan_data1[1]))

In [ ]:
scan_data